In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, StandardScaler, MinMaxScaler, LabelEncoder
from sklearn.impute import SimpleImputer
from imblearn.over_sampling import SMOTE
import featuretools as ft


In [2]:
df = pd.read_csv("../data\jio_mart_items.csv")

print(df.info())
# print(df.head())

print("Пропущенные значения:\n", df.isnull().sum())

print(df.describe())


<>:1: SyntaxWarning: invalid escape sequence '\j'
<>:1: SyntaxWarning: invalid escape sequence '\j'
C:\Users\MaD\AppData\Local\Temp\ipykernel_6188\750029597.py:1: SyntaxWarning: invalid escape sequence '\j'
  df = pd.read_csv("../data\jio_mart_items.csv")


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 162313 entries, 0 to 162312
Data columns (total 5 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   category      162313 non-null  object 
 1   sub_category  162313 non-null  object 
 2   href          162313 non-null  object 
 3   items         162280 non-null  object 
 4   price         162282 non-null  float64
dtypes: float64(1), object(4)
memory usage: 6.2+ MB
None
Пропущенные значения:
 category         0
sub_category     0
href             0
items           33
price           31
dtype: int64
              price
count  1.622820e+05
mean   1.991633e+03
std    1.593479e+04
min    5.000000e+00
25%    2.840000e+02
50%    4.990000e+02
75%    9.990000e+02
max    3.900000e+06


Бизнес-цели:
1. Предсказать категорию продукта (классификация), чтобы рекомендовать новые товары на основе текущей базы.
2. Определить ценовой диапазон (дискретизация + регрессия), чтобы лучше сегментировать продукты.

Технические цели:
Для цели 1: Разработка модели классификации для предсказания категории продукта.
Для цели 2: Разработка модели, предсказывающей ценовой диапазон продукта.


In [3]:
# Удаление бесполезных столбцов
df = df.drop(columns=["Product_ID", "Unnamed: 0"], errors="ignore")

# Обработка пропущенных значений
imputer = SimpleImputer(strategy="most_frequent")  # Для категориальных данных
df = pd.DataFrame(imputer.fit_transform(df), columns=df.columns)

# Преобразование числовых столбцов
numeric_cols = df.select_dtypes(include=["float64", "int64"]).columns
categorical_cols = df.select_dtypes(include=["object"]).columns

# Дискретизация ценового диапазона, разобъём его на 10 категорий
df["Price_Range"] = pd.qcut(df["price"], q=10, labels=False)

# Кодирование категорий
encoder = LabelEncoder()
for col in categorical_cols:
    df[col] = encoder.fit_transform(df[col])

# Проверяем результат
# print(df.head())


In [4]:
# # Построем график распределение категорий чтобы убедится в верной дискретизации
# sns.countplot(data=df, x="Price_Range", palette="viridis")
# plt.title("Распределение значений Price_Range")
# plt.xlabel("Диапазон цен (Price_Range)")
# plt.ylabel("Количество товаров")
# plt.show()


In [5]:
# Разделение данных на X и y для каждой задачи
X = df.drop(columns=["category", "Price_Range"])  # Признаки
y_classification = df["category"]  # Для первой цели (категория продукта)
y_regression = df["Price_Range"]  # Для второй цели (ценовой диапазон)

# Разбиение данных
X_train, X_temp, y_train_class, y_temp_class = train_test_split(X, y_classification, test_size=0.4, stratify=y_classification, random_state=42)
X_val, X_test, y_val_class, y_test_class = train_test_split(X_temp, y_temp_class, test_size=0.5, stratify=y_temp_class, random_state=42)

X_train_reg, X_temp_reg, y_train_reg, y_temp_reg = train_test_split(X, y_regression, test_size=0.4, stratify=y_regression, random_state=42)
X_val_reg, X_test_reg, y_val_reg, y_test_reg = train_test_split(X_temp_reg, y_temp_reg, test_size=0.5, stratify=y_temp_reg, random_state=42)

# Проверяем размеры выборок
print("Train shape (classification):", X_train.shape)
print("Validation shape (classification):", X_val.shape)
print("Test shape (classification):", X_test.shape)


Train shape (classification): (97387, 4)
Validation shape (classification): (32463, 4)
Test shape (classification): (32463, 4)


In [6]:
# Проверяем сбалансированность
print("Распределение классов (Classification):\n", y_train_class.value_counts())

# Применяем SMOTE для балансировки классов
smote = SMOTE(random_state=42)
X_train_balanced, y_train_balanced = smote.fit_resample(X_train, y_train_class)

# Проверяем результат
print("Распределение классов после балансировки:\n", pd.Series(y_train_balanced).value_counts())


Распределение классов (Classification):
 category
4    36201
3    27626
2    15660
1    11413
0     6445
5       42
Name: count, dtype: int64
Распределение классов после балансировки:
 category
4    36201
3    36201
1    36201
2    36201
0    36201
5    36201
Name: count, dtype: int64
